In [1]:
import pandas as pd
import numpy as np
import time
import datetime as dt
import joblib
import pickle

np.random.seed(42)
np.random.RandomState(42)

from pathlib import Path
from scipy import stats
from sklearn import preprocessing
from sklearn.compose import ColumnTransformer
from sklearn.preprocessing import StandardScaler
from sklearn.pipeline import make_pipeline
from sklearn.preprocessing import FunctionTransformer
from sklearn.preprocessing import OneHotEncoder
from sklearn.model_selection import RandomizedSearchCV
from sklearn.metrics import mean_squared_error, r2_score

from catboost import CatBoostRegressor
from xgboost.sklearn import XGBRegressor
from lightgbm import LGBMRegressor
from sklearn.linear_model import Ridge


Links to external data and license

dataset website: https://dev.meteostat.net/bulk/hourly.html#endpoints

dataset 2020 https://bulk.meteostat.net/v2/hourly/2020/07156.csv.gz

dataset 2021 https://bulk.meteostat.net/v2/hourly/2021/07156.csv.gz

license https://dev.meteostat.net/terms.html#license

In [2]:
# load processed external data
fin_ext_data = pd.read_csv(Path("Ext_Data") / "external_data_no_cyc.csv", index_col=0)

In [3]:
# load training and test data
data = pd.read_parquet(Path("data") / "train.parquet")
data1 = pd.read_parquet(Path("data") / "test.parquet")

In [4]:
# convert the date to datetime format
fin_ext_data["date"] = pd.to_datetime(fin_ext_data["date"])
fin_ext_data.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 17416 entries, 0 to 17415
Data columns (total 14 columns):
 #   Column     Non-Null Count  Dtype         
---  ------     --------------  -----         
 0   date       17416 non-null  datetime64[ns]
 1   temp       17416 non-null  float64       
 2   dwpt       17416 non-null  float64       
 3   rhum       17416 non-null  int64         
 4   prcp       17416 non-null  float64       
 5   wdir       17416 non-null  float64       
 6   wspd       17416 non-null  float64       
 7   pres       17416 non-null  float64       
 8   holiday    17416 non-null  int64         
 9   weekend    17416 non-null  int64         
 10  lockdown1  17416 non-null  int64         
 11  lockdown2  17416 non-null  int64         
 12  season     17416 non-null  int64         
 13  is_night   17416 non-null  int64         
dtypes: datetime64[ns](1), float64(6), int64(7)
memory usage: 2.0 MB


In [5]:
# merge training and external data on basis of dates
train_merged = data.merge(fin_ext_data, on='date')

In [6]:
# merge test and external data on basis of dates
test_merged = data1.merge(fin_ext_data, on='date')

In [7]:
# generate target label and features columns from train data
data_tr = train_merged.sort_values(["date", "counter_name"])
y_train = data_tr["log_bike_count"].values
X_train = data_tr.drop(["log_bike_count", "bike_count"], axis=1)

In [8]:
# generate target label and features columns from test data
data_ts = test_merged.sort_values(["date", "counter_name"])
y_test = data_ts["log_bike_count"].values
X_test = data_ts.drop(["log_bike_count", "bike_count"], axis=1)

In [9]:
def _encode_dates(X):
    """
    Breakdown date into components
    in order to apply OneHotEncoding later

    Input:pandas dataframe

    Output: pandas dataframe with new columns

    """
    X = X.copy()
    X.loc[:, "year"] = X["date"].dt.year
    X.loc[:, "month"] = X["date"].dt.month
    X.loc[:, "day"] = X["date"].dt.day
    X.loc[:, "weekday"] = X["date"].dt.weekday
    X.loc[:, "hour"] = X["date"].dt.hour
    return X.drop(columns=["date"])

In [10]:
"""
Apply OneHotEncoding to date and categorical columns
Numerical features are standardized using StandardScaler
Columns like holiday, is_night are already binary so we passthrough them
"""

date_encoder = FunctionTransformer(_encode_dates)
date_cols = _encode_dates(X_train[["date"]]).columns.tolist()
num_features = ['temp', 'dwpt', 'rhum', 'prcp', 'wdir', 'wspd', 'pres']

categorical_encoder = OneHotEncoder(handle_unknown="ignore")
categorical_cols = ["counter_name", "site_name", "season"]

rest_cols = ['holiday', 'weekend', 'is_night', 'lockdown1', 'lockdown2']

preprocessor = ColumnTransformer(
    [
        ("date", OneHotEncoder(handle_unknown="ignore"), date_cols),
        ("cat", categorical_encoder, categorical_cols),
        ("numf", StandardScaler(), num_features),
        ("rem", 'passthrough', rest_cols)
    ]
)

## XGB Regressor

In [11]:
params = {
 "xgbregressor__learning_rate": [0.05, 0.10, 0.15, 0.20],
 "xgbregressor__max_depth": [5, 6, 8, 9, 10, 12],
 "xgbregressor__min_child_weight": [1, 3, 4, 5, 7],
 "xgbregressor__gamma": [0.1, 0.2, 0.3, 0.4],
 "xgbregressor__colsample_bytree": [0.3, 0.4, 0.5, 0.7],
 "xgbregressor__n_estimators": [100, 200, 300, 400, 500]
}

regressor = XGBRegressor()
pipe = make_pipeline(date_encoder, preprocessor, regressor)
rscv = RandomizedSearchCV(pipe, param_distributions=params, n_iter=50,
                          scoring="neg_root_mean_squared_error",
                          n_jobs=-1, cv=5, verbose=3)
rscv.fit(X_train, y_train)

Fitting 5 folds for each of 50 candidates, totalling 250 fits


RandomizedSearchCV(cv=5,
                   estimator=Pipeline(steps=[('functiontransformer',
                                              FunctionTransformer(func=<function _encode_dates at 0x7f8a640971f0>)),
                                             ('columntransformer',
                                              ColumnTransformer(transformers=[('date',
                                                                               OneHotEncoder(handle_unknown='ignore'),
                                                                               ['year',
                                                                                'month',
                                                                                'day',
                                                                                'weekday',
                                                                                'hour']),
                                                                       

In [12]:
# get the best parameters from the RandomizedCV
bestparams = rscv.best_params_
bestparams

{'xgbregressor__n_estimators': 500,
 'xgbregressor__min_child_weight': 7,
 'xgbregressor__max_depth': 10,
 'xgbregressor__learning_rate': 0.1,
 'xgbregressor__gamma': 0.4,
 'xgbregressor__colsample_bytree': 0.7}

In [13]:
# store the pipeline and bestparams
joblib.dump(pipe, 'XGBoostPipeline')
joblib.dump(bestparams, 'XGB_Best_Model')

['XGB_Best_Model']

In [14]:
joblib.load('XGB_Best_Model')

{'xgbregressor__n_estimators': 500,
 'xgbregressor__min_child_weight': 7,
 'xgbregressor__max_depth': 10,
 'xgbregressor__learning_rate': 0.1,
 'xgbregressor__gamma': 0.4,
 'xgbregressor__colsample_bytree': 0.7}

In [15]:
# calulate the rmse and r-squared errors on the fit using best params

rmse_train = mean_squared_error(y_train, rscv.predict(X_train), squared=False)
rmse_test = mean_squared_error(y_test, rscv.predict(X_test), squared=False)
r2_train = r2_score(y_train, rscv.predict(X_train))
r2_test = r2_score(y_test, rscv.predict(X_test))

print(
    f"Train set, RMSE={rmse_train:.7f}"
)
print(
    f"Test set, RMSE={rmse_test:.7f}"
)

print(
    f"Train set, r2 score={r2_train:.7f}"
)
print(
    f"Test set, r2 score={r2_test:.7f}"
)

Train set, RMSE=0.3151528
Test set, RMSE=0.4345230
Train set, r2 score=0.9646067
Test set, r2 score=0.9088303


## CatBoost Regressor

In [16]:
params = {
 "catboostregressor__iterations": [100, 300, 500, 700, 1000],
 "catboostregressor__max_depth": [6, 8, 10],
 "catboostregressor__l2_leaf_reg": [4, 5, 6, 7, 8, 9, 10],
 "catboostregressor__learning_rate": [0.03, 0.05, 0.07, 0.1],
 "catboostregressor__bagging_temperature": [0.3, 0.4, 0.5, 0.7],
 "catboostregressor__random_strength": [3, 4, 5, 6]
}

regressor = CatBoostRegressor()
pipe = make_pipeline(date_encoder, preprocessor, regressor)
rscv = RandomizedSearchCV(pipe, param_distributions=params, n_iter=50,
                          scoring="neg_root_mean_squared_error",
                          n_jobs=-1, cv=5, verbose=3)
rscv.fit(X_train, y_train)

Fitting 5 folds for each of 50 candidates, totalling 250 fits
[CV 1/5] END xgbregressor__colsample_bytree=0.7, xgbregressor__gamma=0.1, xgbregressor__learning_rate=0.05, xgbregressor__max_depth=8, xgbregressor__min_child_weight=7, xgbregressor__n_estimators=100;, score=-0.765 total time=  48.1s
[CV 5/5] END xgbregressor__colsample_bytree=0.5, xgbregressor__gamma=0.1, xgbregressor__learning_rate=0.2, xgbregressor__max_depth=12, xgbregressor__min_child_weight=5, xgbregressor__n_estimators=100;, score=-0.730 total time=  55.8s
[CV 3/5] END xgbregressor__colsample_bytree=0.5, xgbregressor__gamma=0.2, xgbregressor__learning_rate=0.15, xgbregressor__max_depth=6, xgbregressor__min_child_weight=3, xgbregressor__n_estimators=500;, score=-0.691 total time= 2.2min
[CV 4/5] END xgbregressor__colsample_bytree=0.3, xgbregressor__gamma=0.1, xgbregressor__learning_rate=0.2, xgbregressor__max_depth=5, xgbregressor__min_child_weight=5, xgbregressor__n_estimators=200;, score=-0.743 total time=  33.1s
[CV

[CV 3/5] END xgbregressor__colsample_bytree=0.3, xgbregressor__gamma=0.2, xgbregressor__learning_rate=0.1, xgbregressor__max_depth=10, xgbregressor__min_child_weight=4, xgbregressor__n_estimators=100;, score=-0.722 total time=  34.7s
[CV 1/5] END xgbregressor__colsample_bytree=0.5, xgbregressor__gamma=0.1, xgbregressor__learning_rate=0.2, xgbregressor__max_depth=12, xgbregressor__min_child_weight=5, xgbregressor__n_estimators=100;, score=-0.705 total time=  56.5s
[CV 4/5] END xgbregressor__colsample_bytree=0.5, xgbregressor__gamma=0.1, xgbregressor__learning_rate=0.15, xgbregressor__max_depth=9, xgbregressor__min_child_weight=5, xgbregressor__n_estimators=200;, score=-0.663 total time= 1.3min
[CV 2/5] END xgbregressor__colsample_bytree=0.5, xgbregressor__gamma=0.3, xgbregressor__learning_rate=0.1, xgbregressor__max_depth=10, xgbregressor__min_child_weight=5, xgbregressor__n_estimators=100;, score=-0.641 total time=  45.5s
[CV 5/5] END xgbregressor__colsample_bytree=0.5, xgbregressor__g

[CV 1/5] END xgbregressor__colsample_bytree=0.3, xgbregressor__gamma=0.2, xgbregressor__learning_rate=0.1, xgbregressor__max_depth=10, xgbregressor__min_child_weight=4, xgbregressor__n_estimators=100;, score=-0.739 total time=  33.8s
[CV 4/5] END xgbregressor__colsample_bytree=0.3, xgbregressor__gamma=0.2, xgbregressor__learning_rate=0.1, xgbregressor__max_depth=10, xgbregressor__min_child_weight=4, xgbregressor__n_estimators=100;, score=-0.761 total time=  33.5s
[CV 2/5] END xgbregressor__colsample_bytree=0.5, xgbregressor__gamma=0.1, xgbregressor__learning_rate=0.15, xgbregressor__max_depth=9, xgbregressor__min_child_weight=5, xgbregressor__n_estimators=200;, score=-0.637 total time= 1.3min
[CV 5/5] END xgbregressor__colsample_bytree=0.5, xgbregressor__gamma=0.2, xgbregressor__learning_rate=0.15, xgbregressor__max_depth=6, xgbregressor__min_child_weight=3, xgbregressor__n_estimators=500;, score=-0.714 total time= 2.2min
[CV 3/5] END xgbregressor__colsample_bytree=0.5, xgbregressor__g

[CV 5/5] END xgbregressor__colsample_bytree=0.7, xgbregressor__gamma=0.1, xgbregressor__learning_rate=0.05, xgbregressor__max_depth=8, xgbregressor__min_child_weight=7, xgbregressor__n_estimators=100;, score=-0.809 total time=  47.6s
[CV 2/5] END xgbregressor__colsample_bytree=0.5, xgbregressor__gamma=0.1, xgbregressor__learning_rate=0.2, xgbregressor__max_depth=12, xgbregressor__min_child_weight=5, xgbregressor__n_estimators=100;, score=-0.637 total time=  55.6s
[CV 1/5] END xgbregressor__colsample_bytree=0.5, xgbregressor__gamma=0.2, xgbregressor__learning_rate=0.15, xgbregressor__max_depth=6, xgbregressor__min_child_weight=3, xgbregressor__n_estimators=500;, score=-0.700 total time= 2.2min
[CV 3/5] END xgbregressor__colsample_bytree=0.3, xgbregressor__gamma=0.1, xgbregressor__learning_rate=0.2, xgbregressor__max_depth=5, xgbregressor__min_child_weight=5, xgbregressor__n_estimators=200;, score=-0.732 total time=  33.2s
[CV 5/5] END xgbregressor__colsample_bytree=0.4, xgbregressor__ga

[CV 2/5] END xgbregressor__colsample_bytree=0.7, xgbregressor__gamma=0.1, xgbregressor__learning_rate=0.05, xgbregressor__max_depth=8, xgbregressor__min_child_weight=7, xgbregressor__n_estimators=100;, score=-0.668 total time=  47.8s
[CV 4/5] END xgbregressor__colsample_bytree=0.5, xgbregressor__gamma=0.1, xgbregressor__learning_rate=0.2, xgbregressor__max_depth=12, xgbregressor__min_child_weight=5, xgbregressor__n_estimators=100;, score=-0.687 total time=  55.4s
[CV 5/5] END xgbregressor__colsample_bytree=0.5, xgbregressor__gamma=0.1, xgbregressor__learning_rate=0.15, xgbregressor__max_depth=9, xgbregressor__min_child_weight=5, xgbregressor__n_estimators=200;, score=-0.725 total time= 1.4min
[CV 3/5] END xgbregressor__colsample_bytree=0.5, xgbregressor__gamma=0.3, xgbregressor__learning_rate=0.1, xgbregressor__max_depth=10, xgbregressor__min_child_weight=5, xgbregressor__n_estimators=100;, score=-0.696 total time=  45.4s
[CV 1/5] END xgbregressor__colsample_bytree=0.3, xgbregressor__g

...

485:	learn: 0.4372007	total: 20.8s	remaining: 22s
486:	learn: 0.4368849	total: 20.8s	remaining: 22s
487:	learn: 0.4367294	total: 20.9s	remaining: 21.9s
488:	learn: 0.4364913	total: 20.9s	remaining: 21.9s
489:	learn: 0.4363200	total: 21s	remaining: 21.8s
490:	learn: 0.4361997	total: 21s	remaining: 21.8s
491:	learn: 0.4358913	total: 21.1s	remaining: 21.7s
492:	learn: 0.4357468	total: 21.1s	remaining: 21.7s
493:	learn: 0.4355854	total: 21.1s	remaining: 21.7s
494:	learn: 0.4353749	total: 21.2s	remaining: 21.6s
495:	learn: 0.4352185	total: 21.2s	remaining: 21.6s
496:	learn: 0.4349386	total: 21.3s	remaining: 21.5s
497:	learn: 0.4347734	total: 21.3s	remaining: 21.5s
498:	learn: 0.4345105	total: 21.3s	remaining: 21.4s
499:	learn: 0.4343240	total: 21.4s	remaining: 21.4s
500:	learn: 0.4341741	total: 21.4s	remaining: 21.3s
501:	learn: 0.4339796	total: 21.5s	remaining: 21.3s
502:	learn: 0.4337001	total: 21.5s	remaining: 21.3s
503:	learn: 0.4333508	total: 21.6s	remaining: 21.2s
504:	learn: 0.433162

645:	learn: 0.4110540	total: 27.6s	remaining: 15.1s
646:	learn: 0.4108998	total: 27.7s	remaining: 15.1s
647:	learn: 0.4107685	total: 27.7s	remaining: 15.1s
648:	learn: 0.4106708	total: 27.8s	remaining: 15s
649:	learn: 0.4105623	total: 27.8s	remaining: 15s
650:	learn: 0.4104332	total: 27.9s	remaining: 14.9s
651:	learn: 0.4103138	total: 27.9s	remaining: 14.9s
652:	learn: 0.4101905	total: 27.9s	remaining: 14.8s
653:	learn: 0.4100938	total: 28s	remaining: 14.8s
654:	learn: 0.4099926	total: 28s	remaining: 14.8s
655:	learn: 0.4098866	total: 28.1s	remaining: 14.7s
656:	learn: 0.4097319	total: 28.1s	remaining: 14.7s
657:	learn: 0.4096561	total: 28.2s	remaining: 14.6s
658:	learn: 0.4095725	total: 28.2s	remaining: 14.6s
659:	learn: 0.4094068	total: 28.2s	remaining: 14.5s
660:	learn: 0.4092497	total: 28.3s	remaining: 14.5s
661:	learn: 0.4091645	total: 28.3s	remaining: 14.5s
662:	learn: 0.4090783	total: 28.4s	remaining: 14.4s
663:	learn: 0.4089723	total: 28.4s	remaining: 14.4s
664:	learn: 0.408822

804:	learn: 0.3928930	total: 34.4s	remaining: 8.34s
805:	learn: 0.3928020	total: 34.5s	remaining: 8.3s
806:	learn: 0.3926683	total: 34.5s	remaining: 8.26s
807:	learn: 0.3925924	total: 34.6s	remaining: 8.21s
808:	learn: 0.3924718	total: 34.6s	remaining: 8.17s
809:	learn: 0.3923891	total: 34.6s	remaining: 8.13s
810:	learn: 0.3923107	total: 34.7s	remaining: 8.08s
811:	learn: 0.3921910	total: 34.7s	remaining: 8.04s
812:	learn: 0.3920773	total: 34.8s	remaining: 8s
813:	learn: 0.3920001	total: 34.8s	remaining: 7.95s
814:	learn: 0.3919337	total: 34.9s	remaining: 7.91s
815:	learn: 0.3918241	total: 34.9s	remaining: 7.87s
816:	learn: 0.3917069	total: 34.9s	remaining: 7.83s
817:	learn: 0.3915946	total: 35s	remaining: 7.78s
818:	learn: 0.3914998	total: 35s	remaining: 7.74s
819:	learn: 0.3914416	total: 35.1s	remaining: 7.7s
820:	learn: 0.3913372	total: 35.1s	remaining: 7.65s
821:	learn: 0.3912584	total: 35.2s	remaining: 7.61s
822:	learn: 0.3911864	total: 35.2s	remaining: 7.57s
823:	learn: 0.3910418

964:	learn: 0.3795404	total: 41.3s	remaining: 1.5s
965:	learn: 0.3794588	total: 41.4s	remaining: 1.46s
966:	learn: 0.3794101	total: 41.4s	remaining: 1.41s
967:	learn: 0.3793359	total: 41.4s	remaining: 1.37s
968:	learn: 0.3792721	total: 41.5s	remaining: 1.33s
969:	learn: 0.3791943	total: 41.5s	remaining: 1.28s
970:	learn: 0.3791366	total: 41.6s	remaining: 1.24s
971:	learn: 0.3790592	total: 41.6s	remaining: 1.2s
972:	learn: 0.3789722	total: 41.6s	remaining: 1.16s
973:	learn: 0.3788912	total: 41.7s	remaining: 1.11s
974:	learn: 0.3788304	total: 41.7s	remaining: 1.07s
975:	learn: 0.3787789	total: 41.8s	remaining: 1.03s
976:	learn: 0.3787129	total: 41.8s	remaining: 984ms
977:	learn: 0.3786294	total: 41.9s	remaining: 942ms
978:	learn: 0.3785754	total: 41.9s	remaining: 899ms
979:	learn: 0.3785143	total: 41.9s	remaining: 856ms
980:	learn: 0.3784010	total: 42s	remaining: 813ms
981:	learn: 0.3782795	total: 42s	remaining: 770ms
982:	learn: 0.3782137	total: 42.1s	remaining: 728ms
983:	learn: 0.3781

RandomizedSearchCV(cv=5,
                   estimator=Pipeline(steps=[('functiontransformer',
                                              FunctionTransformer(func=<function _encode_dates at 0x7f8a640971f0>)),
                                             ('columntransformer',
                                              ColumnTransformer(transformers=[('date',
                                                                               OneHotEncoder(handle_unknown='ignore'),
                                                                               ['year',
                                                                                'month',
                                                                                'day',
                                                                                'weekday',
                                                                                'hour']),
                                                                       

In [17]:
# get the best parameters from the RandomizedCV
bestparams = rscv.best_params_
bestparams

{'catboostregressor__random_strength': 3,
 'catboostregressor__max_depth': 10,
 'catboostregressor__learning_rate': 0.07,
 'catboostregressor__l2_leaf_reg': 6,
 'catboostregressor__iterations': 1000,
 'catboostregressor__bagging_temperature': 0.4}

In [18]:
# store the pipeline and bestparams
joblib.dump(pipe, 'CATBoost')
joblib.dump(bestparams, 'CatB_Best_Model')

['CatB_Best_Model']

In [19]:
joblib.load('CatB_Best_Model')

{'catboostregressor__random_strength': 3,
 'catboostregressor__max_depth': 10,
 'catboostregressor__learning_rate': 0.07,
 'catboostregressor__l2_leaf_reg': 6,
 'catboostregressor__iterations': 1000,
 'catboostregressor__bagging_temperature': 0.4}

In [20]:
# calulate the rmse and r-squared errors on the fit using best params

rmse_train = mean_squared_error(y_train, rscv.predict(X_train), squared=False)
rmse_test = mean_squared_error(y_test, rscv.predict(X_test), squared=False)
r2_train = r2_score(y_train, rscv.predict(X_train))
r2_test = r2_score(y_test, rscv.predict(X_test))

print(
    f"Train set, RMSE={rmse_train:.7f}"
)
print(
    f"Test set, RMSE={rmse_test:.7f}"
)

print(
    f"Train set, r2 score={r2_train:.7f}"
)
print(
    f"Test set, r2 score={r2_test:.7f}"
)

Train set, RMSE=0.3770412
Test set, RMSE=0.4388059
Train set, r2 score=0.9493410
Test set, r2 score=0.9070241


## LightGBM

In [21]:
params = {
    "lgbmregressor__learning_rate": [0.01, 0.05, 0.1, 0.2],
    "lgbmregressor__max_depth": [5, 6, 8, 9, 10, 12],
    "lgbmregressor__num_leaves": [50, 100, 200, 400, 800, 1000],
    "lgbmregressor__min_data_in_leaf": [50, 100, 200, 500],
    "lgbmregressor__lambda_l2": [1, 3, 5, 7, 9],
    "lgbmregressor__n_estimators": [1000, 5000, 10000]
}

regressor = LGBMRegressor()
pipe = make_pipeline(date_encoder, preprocessor, regressor)
rscv = RandomizedSearchCV(pipe, param_distributions=params, n_iter=40,
                          scoring="neg_root_mean_squared_error",
                          n_jobs=-1, cv=5, verbose=3)
rscv.fit(X_train, y_train)

Fitting 5 folds for each of 40 candidates, totalling 200 fits
352:	learn: 0.6312195	total: 39.2s	remaining: 38.6s
353:	learn: 0.6309700	total: 39.3s	remaining: 38.4s
354:	learn: 0.6307203	total: 39.4s	remaining: 38.3s
355:	learn: 0.6302898	total: 39.4s	remaining: 38.1s
356:	learn: 0.6297926	total: 39.5s	remaining: 37.9s
357:	learn: 0.6292082	total: 39.6s	remaining: 37.8s
358:	learn: 0.6287930	total: 39.7s	remaining: 37.7s
359:	learn: 0.6285283	total: 39.8s	remaining: 37.6s
360:	learn: 0.6279571	total: 39.9s	remaining: 37.5s
361:	learn: 0.6274903	total: 40s	remaining: 37.3s
362:	learn: 0.6268070	total: 40s	remaining: 37.2s
363:	learn: 0.6260170	total: 40.1s	remaining: 37s
364:	learn: 0.6256344	total: 40.2s	remaining: 36.9s
365:	learn: 0.6251366	total: 40.3s	remaining: 36.8s
366:	learn: 0.6247165	total: 40.4s	remaining: 36.6s
367:	learn: 0.6243483	total: 40.5s	remaining: 36.6s
368:	learn: 0.6240749	total: 40.7s	remaining: 36.5s
369:	learn: 0.6237696	total: 40.8s	remaining: 36.4s
370:	lea

604:	learn: 0.5478297	total: 1m 3s	remaining: 9.96s
605:	learn: 0.5476236	total: 1m 3s	remaining: 9.84s
606:	learn: 0.5473767	total: 1m 3s	remaining: 9.74s
607:	learn: 0.5471823	total: 1m 3s	remaining: 9.63s
608:	learn: 0.5469981	total: 1m 3s	remaining: 9.52s
609:	learn: 0.5466496	total: 1m 3s	remaining: 9.4s
610:	learn: 0.5464366	total: 1m 3s	remaining: 9.29s
611:	learn: 0.5462076	total: 1m 3s	remaining: 9.18s
612:	learn: 0.5459567	total: 1m 3s	remaining: 9.07s
613:	learn: 0.5457257	total: 1m 4s	remaining: 8.96s
614:	learn: 0.5454140	total: 1m 4s	remaining: 8.86s
615:	learn: 0.5451843	total: 1m 4s	remaining: 8.76s
616:	learn: 0.5450156	total: 1m 4s	remaining: 8.65s
617:	learn: 0.5446662	total: 1m 4s	remaining: 8.54s
618:	learn: 0.5444909	total: 1m 4s	remaining: 8.44s
619:	learn: 0.5442278	total: 1m 4s	remaining: 8.33s
620:	learn: 0.5440232	total: 1m 4s	remaining: 8.22s
621:	learn: 0.5436344	total: 1m 4s	remaining: 8.12s
622:	learn: 0.5434449	total: 1m 4s	remaining: 8s
623:	learn: 0.54

14:	learn: 1.3203738	total: 3.4s	remaining: 1m 4s
15:	learn: 1.3034275	total: 3.62s	remaining: 1m 4s
16:	learn: 1.2851153	total: 3.81s	remaining: 1m 3s
17:	learn: 1.2689934	total: 4.09s	remaining: 1m 4s
18:	learn: 1.2530212	total: 4.3s	remaining: 1m 3s
19:	learn: 1.2379961	total: 4.53s	remaining: 1m 3s
20:	learn: 1.2224696	total: 4.79s	remaining: 1m 3s
21:	learn: 1.2085195	total: 5s	remaining: 1m 3s
22:	learn: 1.1949496	total: 5.22s	remaining: 1m 2s
23:	learn: 1.1835510	total: 5.49s	remaining: 1m 3s
24:	learn: 1.1704294	total: 5.71s	remaining: 1m 2s
25:	learn: 1.1595972	total: 5.98s	remaining: 1m 2s
26:	learn: 1.1469110	total: 6.21s	remaining: 1m 2s
27:	learn: 1.1367477	total: 6.49s	remaining: 1m 3s
28:	learn: 1.1266368	total: 6.71s	remaining: 1m 2s
29:	learn: 1.1162602	total: 6.99s	remaining: 1m 2s
30:	learn: 1.1065676	total: 7.23s	remaining: 1m 2s
31:	learn: 1.0963469	total: 7.4s	remaining: 1m 1s
32:	learn: 1.0870967	total: 7.71s	remaining: 1m 2s
33:	learn: 1.0771058	total: 7.92s	rem

435:	learn: 0.6031341	total: 42s	remaining: 25.4s
436:	learn: 0.6027865	total: 42s	remaining: 25.3s
437:	learn: 0.6022685	total: 42.1s	remaining: 25.2s
438:	learn: 0.6019208	total: 42.3s	remaining: 25.1s
439:	learn: 0.6016479	total: 42.3s	remaining: 25s
440:	learn: 0.6013878	total: 42.4s	remaining: 24.9s
441:	learn: 0.6009657	total: 42.5s	remaining: 24.8s
442:	learn: 0.6006408	total: 42.6s	remaining: 24.7s
443:	learn: 0.6003564	total: 42.6s	remaining: 24.6s
444:	learn: 0.5999159	total: 42.7s	remaining: 24.5s
445:	learn: 0.5995673	total: 42.8s	remaining: 24.4s
446:	learn: 0.5992081	total: 42.9s	remaining: 24.3s
447:	learn: 0.5989296	total: 42.9s	remaining: 24.2s
448:	learn: 0.5984858	total: 43s	remaining: 24.1s
449:	learn: 0.5980483	total: 43.1s	remaining: 23.9s
450:	learn: 0.5977359	total: 43.2s	remaining: 23.8s
451:	learn: 0.5973884	total: 43.2s	remaining: 23.7s
452:	learn: 0.5968948	total: 43.3s	remaining: 23.6s
453:	learn: 0.5962802	total: 43.4s	remaining: 23.5s
454:	learn: 0.596015

683:	learn: 0.5353757	total: 51.6s	remaining: 23.8s
684:	learn: 0.5352422	total: 51.6s	remaining: 23.7s
685:	learn: 0.5350806	total: 51.7s	remaining: 23.6s
686:	learn: 0.5348632	total: 51.7s	remaining: 23.6s
687:	learn: 0.5346451	total: 51.8s	remaining: 23.5s
688:	learn: 0.5344733	total: 51.8s	remaining: 23.4s
689:	learn: 0.5343399	total: 51.9s	remaining: 23.3s
690:	learn: 0.5342174	total: 51.9s	remaining: 23.2s
691:	learn: 0.5340168	total: 52s	remaining: 23.1s
692:	learn: 0.5338564	total: 52s	remaining: 23s
693:	learn: 0.5335181	total: 52.1s	remaining: 23s
694:	learn: 0.5333656	total: 52.1s	remaining: 22.9s
695:	learn: 0.5331576	total: 52.2s	remaining: 22.8s
696:	learn: 0.5330119	total: 52.2s	remaining: 22.7s
697:	learn: 0.5328202	total: 52.3s	remaining: 22.6s
698:	learn: 0.5326120	total: 52.3s	remaining: 22.5s
699:	learn: 0.5323646	total: 52.4s	remaining: 22.5s
700:	learn: 0.5321974	total: 52.4s	remaining: 22.4s
701:	learn: 0.5319949	total: 52.5s	remaining: 22.3s
702:	learn: 0.531835

...

[CV 4/5] END catboostregressor__bagging_temperature=0.3, catboostregressor__iterations=1000, catboostregressor__l2_leaf_reg=7, catboostregressor__learning_rate=0.03, catboostregressor__max_depth=8, catboostregressor__random_strength=6;, score=-0.672 total time= 1.1min
[LightGBM] [Warning] min_data_in_leaf is set=200, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=200
[LightGBM] [Warning] lambda_l2 is set=7, reg_lambda=0.0 will be ignored. Current value: lambda_l2=7
[CV 2/5] END lgbmregressor__lambda_l2=7, lgbmregressor__learning_rate=0.2, lgbmregressor__max_depth=9, lgbmregressor__min_data_in_leaf=200, lgbmregressor__n_estimators=1000, lgbmregressor__num_leaves=800;, score=-0.647 total time=  28.2s
[LightGBM] [Warning] min_data_in_leaf is set=100, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=100
[LightGBM] [Warning] lambda_l2 is set=1, reg_lambda=0.0 will be ignored. Current value: lambda_l2=1
[CV 4/5] END lgbmregressor__lambda_l2=1, lgbm

509:	learn: 0.5710604	total: 46.7s	remaining: 17.4s
510:	learn: 0.5708515	total: 46.8s	remaining: 17.3s
511:	learn: 0.5705529	total: 46.9s	remaining: 17.2s
512:	learn: 0.5701934	total: 47s	remaining: 17.1s
513:	learn: 0.5698850	total: 47.1s	remaining: 17s
514:	learn: 0.5696663	total: 47.2s	remaining: 16.9s
515:	learn: 0.5694389	total: 47.2s	remaining: 16.8s
516:	learn: 0.5690548	total: 47.3s	remaining: 16.8s
517:	learn: 0.5686115	total: 47.4s	remaining: 16.7s
518:	learn: 0.5682066	total: 47.5s	remaining: 16.6s
519:	learn: 0.5677336	total: 47.5s	remaining: 16.4s
520:	learn: 0.5672672	total: 47.6s	remaining: 16.4s
521:	learn: 0.5669581	total: 47.7s	remaining: 16.3s
522:	learn: 0.5667108	total: 47.8s	remaining: 16.2s
523:	learn: 0.5664326	total: 47.9s	remaining: 16.1s
524:	learn: 0.5662331	total: 48s	remaining: 16s
525:	learn: 0.5658654	total: 48s	remaining: 15.9s
526:	learn: 0.5655531	total: 48.1s	remaining: 15.8s
527:	learn: 0.5652060	total: 48.2s	remaining: 15.7s
528:	learn: 0.5649145	

47:	learn: 0.8670126	total: 3.67s	remaining: 3.98s
48:	learn: 0.8603693	total: 3.8s	remaining: 3.95s
49:	learn: 0.8573689	total: 3.9s	remaining: 3.9s
50:	learn: 0.8537105	total: 4s	remaining: 3.84s
51:	learn: 0.8480117	total: 4.1s	remaining: 3.79s
52:	learn: 0.8449896	total: 4.16s	remaining: 3.69s
53:	learn: 0.8423416	total: 4.21s	remaining: 3.59s
54:	learn: 0.8403520	total: 4.29s	remaining: 3.51s
55:	learn: 0.8377964	total: 4.34s	remaining: 3.41s
56:	learn: 0.8340729	total: 4.41s	remaining: 3.32s
57:	learn: 0.8316938	total: 4.46s	remaining: 3.23s
58:	learn: 0.8290871	total: 4.57s	remaining: 3.18s
59:	learn: 0.8266952	total: 4.64s	remaining: 3.09s
60:	learn: 0.8243175	total: 4.68s	remaining: 2.99s
61:	learn: 0.8221768	total: 4.76s	remaining: 2.92s
62:	learn: 0.8192536	total: 4.86s	remaining: 2.86s
63:	learn: 0.8163289	total: 4.91s	remaining: 2.76s
64:	learn: 0.8133593	total: 4.99s	remaining: 2.69s
65:	learn: 0.8098608	total: 5.03s	remaining: 2.59s
66:	learn: 0.8068482	total: 5.1s	remai

[LightGBM] [Warning] min_data_in_leaf is set=200, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=200
[LightGBM] [Warning] lambda_l2 is set=7, reg_lambda=0.0 will be ignored. Current value: lambda_l2=7
596:	learn: 0.5494215	total: 50.1s	remaining: 33.9s
597:	learn: 0.5492693	total: 50.2s	remaining: 33.8s
598:	learn: 0.5490105	total: 50.3s	remaining: 33.7s
599:	learn: 0.5487267	total: 50.4s	remaining: 33.6s
600:	learn: 0.5484306	total: 50.5s	remaining: 33.5s
601:	learn: 0.5482186	total: 50.6s	remaining: 33.4s
602:	learn: 0.5479440	total: 50.6s	remaining: 33.3s
603:	learn: 0.5477497	total: 50.7s	remaining: 33.2s
604:	learn: 0.5475590	total: 50.8s	remaining: 33.1s
605:	learn: 0.5473603	total: 50.8s	remaining: 33s
606:	learn: 0.5471454	total: 50.9s	remaining: 32.9s
607:	learn: 0.5469588	total: 51s	remaining: 32.9s
608:	learn: 0.5467117	total: 51s	remaining: 32.8s
609:	learn: 0.5464412	total: 51.2s	remaining: 32.7s
610:	learn: 0.5460711	total: 51.3s	remaining: 32.6s
61

RandomizedSearchCV(cv=5,
                   estimator=Pipeline(steps=[('functiontransformer',
                                              FunctionTransformer(func=<function _encode_dates at 0x7f8a640971f0>)),
                                             ('columntransformer',
                                              ColumnTransformer(transformers=[('date',
                                                                               OneHotEncoder(handle_unknown='ignore'),
                                                                               ['year',
                                                                                'month',
                                                                                'day',
                                                                                'weekday',
                                                                                'hour']),
                                                                       

In [22]:
# get the best parameters from the RandomizedCV
bestparams = rscv.best_params_
bestparams

{'lgbmregressor__num_leaves': 100,
 'lgbmregressor__n_estimators': 5000,
 'lgbmregressor__min_data_in_leaf': 200,
 'lgbmregressor__max_depth': 12,
 'lgbmregressor__learning_rate': 0.05,
 'lgbmregressor__lambda_l2': 7}

In [23]:
# store the pipeline and bestparams
joblib.dump(pipe, 'LightGBM')
joblib.dump(bestparams, 'LightGBM_Best_Model')

['LightGBM_Best_Model']

In [24]:
joblib.load('LightGBM_Best_Model')

{'lgbmregressor__num_leaves': 100,
 'lgbmregressor__n_estimators': 5000,
 'lgbmregressor__min_data_in_leaf': 200,
 'lgbmregressor__max_depth': 12,
 'lgbmregressor__learning_rate': 0.05,
 'lgbmregressor__lambda_l2': 7}

In [25]:
# calulate the rmse and r-squared errors on the fit using best params

rmse_train = mean_squared_error(y_train, rscv.predict(X_train), squared=False)
rmse_test = mean_squared_error(y_test, rscv.predict(X_test), squared=False)
r2_train = r2_score(y_train, rscv.predict(X_train))
r2_test = r2_score(y_test, rscv.predict(X_test))

print(
    f"Train set, RMSE={rmse_train:.7f}"
)
print(
    f"Test set, RMSE={rmse_test:.7f}"
)

print(
    f"Train set, r2 score={r2_train:.7f}"
)
print(
    f"Test set, r2 score={r2_test:.7f}"
)

973:	learn: 0.4899639	total: 1m 12s	remaining: 1.93s
974:	learn: 0.4898468	total: 1m 12s	remaining: 1.85s
975:	learn: 0.4897557	total: 1m 12s	remaining: 1.78s
976:	learn: 0.4896187	total: 1m 12s	remaining: 1.7s
977:	learn: 0.4895305	total: 1m 12s	remaining: 1.63s
978:	learn: 0.4894412	total: 1m 12s	remaining: 1.55s
979:	learn: 0.4893632	total: 1m 12s	remaining: 1.48s
980:	learn: 0.4892425	total: 1m 12s	remaining: 1.41s
981:	learn: 0.4891338	total: 1m 12s	remaining: 1.33s
982:	learn: 0.4890490	total: 1m 12s	remaining: 1.26s
983:	learn: 0.4889453	total: 1m 12s	remaining: 1.18s
984:	learn: 0.4888191	total: 1m 12s	remaining: 1.11s
985:	learn: 0.4887105	total: 1m 12s	remaining: 1.03s
986:	learn: 0.4886045	total: 1m 12s	remaining: 960ms
987:	learn: 0.4884880	total: 1m 12s	remaining: 886ms
988:	learn: 0.4884006	total: 1m 12s	remaining: 811ms
989:	learn: 0.4883012	total: 1m 13s	remaining: 737ms
990:	learn: 0.4881894	total: 1m 13s	remaining: 663ms
991:	learn: 0.4881065	total: 1m 13s	remaining: 

552:	learn: 0.5591522	total: 59.4s	remaining: 15.8s
553:	learn: 0.5587396	total: 59.5s	remaining: 15.7s
554:	learn: 0.5585102	total: 59.5s	remaining: 15.6s
555:	learn: 0.5583033	total: 59.6s	remaining: 15.4s
556:	learn: 0.5581026	total: 59.7s	remaining: 15.3s
557:	learn: 0.5578918	total: 59.8s	remaining: 15.2s
558:	learn: 0.5575100	total: 59.9s	remaining: 15.1s
559:	learn: 0.5573247	total: 60s	remaining: 15s
560:	learn: 0.5571387	total: 1m	remaining: 14.9s
561:	learn: 0.5569621	total: 1m	remaining: 14.8s
562:	learn: 0.5564554	total: 1m	remaining: 14.7s
563:	learn: 0.5562278	total: 1m	remaining: 14.6s
564:	learn: 0.5560943	total: 1m	remaining: 14.5s
565:	learn: 0.5557080	total: 1m	remaining: 14.3s
566:	learn: 0.5555298	total: 1m	remaining: 14.2s
567:	learn: 0.5552382	total: 1m	remaining: 14.1s
568:	learn: 0.5550196	total: 1m	remaining: 14s
569:	learn: 0.5548592	total: 1m	remaining: 13.9s
570:	learn: 0.5546441	total: 1m	remaining: 13.8s
571:	learn: 0.5543462	total: 1m 1s	remaining: 13.7s

99:	learn: 0.7437443	total: 7.02s	remaining: 0us
[CV 5/5] END catboostregressor__bagging_temperature=0.7, catboostregressor__iterations=100, catboostregressor__l2_leaf_reg=8, catboostregressor__learning_rate=0.07, catboostregressor__max_depth=6, catboostregressor__random_strength=5;, score=-0.905 total time=   8.1s
[LightGBM] [Warning] min_data_in_leaf is set=50, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=50
[LightGBM] [Warning] lambda_l2 is set=7, reg_lambda=0.0 will be ignored. Current value: lambda_l2=7
[CV 3/5] END lgbmregressor__lambda_l2=7, lgbmregressor__learning_rate=0.05, lgbmregressor__max_depth=5, lgbmregressor__min_data_in_leaf=50, lgbmregressor__n_estimators=1000, lgbmregressor__num_leaves=200;, score=-0.696 total time=  18.5s
[LightGBM] [Warning] min_data_in_leaf is set=100, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=100
[LightGBM] [Warning] lambda_l2 is set=1, reg_lambda=0.0 will be ignored. Current value: lambda_l2=1

Train set, RMSE=0.3164387
Test set, RMSE=0.4464985
Train set, r2 score=0.9643173
Test set, r2 score=0.9037357


## Ridge Regression

For Ridge regression we have used a different external data file which has same columns as above but also hour and month data encoded as cyclical features. The above algorithms don't use the same data as the cyclical encoding doesn't work too well with decision tree algorithms.

In [26]:
# load processed external data
fin_ext_data_cyc = pd.read_csv("/Users/madhuranirale/Desktop/Project/Python_DS_Project/external_data_with_cyc.csv", index_col=0)

In [27]:
# convert the date to datetime format
fin_ext_data_cyc["date"] = pd.to_datetime(fin_ext_data["date"])
fin_ext_data_cyc.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 17416 entries, 0 to 17415
Data columns (total 18 columns):
 #   Column     Non-Null Count  Dtype         
---  ------     --------------  -----         
 0   date       17416 non-null  datetime64[ns]
 1   temp       17416 non-null  float64       
 2   dwpt       17416 non-null  float64       
 3   rhum       17416 non-null  int64         
 4   prcp       17416 non-null  float64       
 5   wdir       17416 non-null  float64       
 6   wspd       17416 non-null  float64       
 7   pres       17416 non-null  float64       
 8   holiday    17416 non-null  int64         
 9   weekend    17416 non-null  int64         
 10  lockdown1  17416 non-null  int64         
 11  lockdown2  17416 non-null  int64         
 12  season     17416 non-null  int64         
 13  is_night   17416 non-null  int64         
 14  hour_sin   17416 non-null  float64       
 15  hour_cos   17416 non-null  float64       
 16  month_sin  17416 non-null  float64      

In [28]:
# merge training and external data on basis of dates
train_merged = data.merge(fin_ext_data_cyc, on='date')

In [29]:
# merge test and external data on basis of dates
test_merged = data1.merge(fin_ext_data_cyc, on='date')

In [30]:
# generate target label and features columns from train data
data_tr = train_merged.sort_values(["date", "counter_name"])
y_train = data_tr["log_bike_count"].values
X_train = data_tr.drop(["log_bike_count", "bike_count"], axis=1)

In [31]:
# generate target label and features columns from test data
data_ts = test_merged.sort_values(["date", "counter_name"])
y_test = data_ts["log_bike_count"].values
X_test = data_ts.drop(["log_bike_count", "bike_count"], axis=1)

In [32]:
"""
Apply OneHotEncoding to date and categorical columns
Numerical features are standardized using StandardScaler
Columns like holiday, is_night are already binary so we passthrough them
We also don't enocde the cyclical columns
"""

date_encoder = FunctionTransformer(_encode_dates)
date_cols = _encode_dates(X_train[["date"]]).columns.tolist()
num_features = ['temp', 'dwpt', 'rhum', 'prcp', 'wdir', 'wspd', 'pres']

categorical_encoder = OneHotEncoder(handle_unknown="ignore")
categorical_cols = ["counter_name", "site_name", "season"]

rest_cols = ['holiday', 'weekend', 'is_night', 'lockdown1', 'lockdown2', 'hour_sin',
            'hour_cos', 'month_sin', 'month_cos']

preprocessor = ColumnTransformer(
    [
        ("date", OneHotEncoder(handle_unknown="ignore"), date_cols),
        ("cat", categorical_encoder, categorical_cols),
        ("numf", StandardScaler(), num_features),
        ("rem", 'passthrough', rest_cols)
    ]
)

In [33]:
params = {
 'ridge__alpha': [1,0.1,0.01,0.001,0.0001,0],
 "ridge__fit_intercept": [True, False],
 "ridge__solver": ['svd', 'cholesky', 'lsqr', 'sparse_cg', 'sag', 'saga']
}

regressor = Ridge()
pipe = make_pipeline(date_encoder, preprocessor, regressor)
rscv = RandomizedSearchCV(pipe, param_distributions=params, n_iter=50, scoring="neg_root_mean_squared_error", n_jobs=-1, cv=5, verbose=3)
rscv.fit(X_train, y_train)

Fitting 5 folds for each of 50 candidates, totalling 250 fits


/Users/madhuranirale/opt/anaconda3/lib/python3.9/site-packages/sklearn/linear_model/_ridge.py:729: UserWarning: "sag" solver requires many iterations to fit an intercept with sparse inputs. Either set the solver to "auto" or "sparse_cg", or set a low "tol" and a high "max_iter" (especially if inputs are not standardized).
  warnings.warn(
/Users/madhuranirale/opt/anaconda3/lib/python3.9/site-packages/sklearn/linear_model/_ridge.py:729: UserWarning: "sag" solver requires many iterations to fit an intercept with sparse inputs. Either set the solver to "auto" or "sparse_cg", or set a low "tol" and a high "max_iter" (especially if inputs are not standardized).
  warnings.warn(
/Users/madhuranirale/opt/anaconda3/lib/python3.9/site-packages/sklearn/linear_model/_ridge.py:729: UserWarning: "sag" solver requires many iterations to fit an intercept with sparse inputs. Either set the solver to "auto" or "sparse_cg", or set a low "tol" and a high "max_iter" (especially if inputs are not standardi

[CV 4/5] END ridge__alpha=0.01, ridge__fit_intercept=False, ridge__solver=svd;, score=nan total time=   0.9s
[CV 5/5] END ridge__alpha=0, ridge__fit_intercept=True, ridge__solver=sparse_cg;, score=-0.958 total time=   1.5s
[CV 3/5] END ridge__alpha=0, ridge__fit_intercept=True, ridge__solver=svd;, score=nan total time=   0.8s
[CV 4/5] END ridge__alpha=0, ridge__fit_intercept=True, ridge__solver=svd;, score=nan total time=   0.7s
[CV 1/5] END ridge__alpha=0.001, ridge__fit_intercept=False, ridge__solver=sparse_cg;, score=-1.351 total time=   1.4s
[CV 4/5] END ridge__alpha=0.001, ridge__fit_intercept=False, ridge__solver=sparse_cg;, score=-1.487 total time=   1.3s
[CV 2/5] END ridge__alpha=0.1, ridge__fit_intercept=False, ridge__solver=sparse_cg;, score=-0.855 total time=   1.4s
[CV 2/5] END ridge__alpha=1, ridge__fit_intercept=False, ridge__solver=sparse_cg;, score=-0.855 total time=   1.7s
[CV 2/5] END ridge__alpha=0.001, ridge__fit_intercept=True, ridge__solver=sparse_cg;, score=-0.83

/Users/madhuranirale/opt/anaconda3/lib/python3.9/site-packages/joblib/externals/loky/process_executor.py:702: UserWarning: A worker stopped while some jobs were given to the executor. This can be caused by a too short worker timeout or by a memory leak.
  warnings.warn(
/Users/madhuranirale/opt/anaconda3/lib/python3.9/site-packages/sklearn/linear_model/_ridge.py:729: UserWarning: "sag" solver requires many iterations to fit an intercept with sparse inputs. Either set the solver to "auto" or "sparse_cg", or set a low "tol" and a high "max_iter" (especially if inputs are not standardized).
  warnings.warn(
/Users/madhuranirale/opt/anaconda3/lib/python3.9/site-packages/sklearn/linear_model/_ridge.py:729: UserWarning: "sag" solver requires many iterations to fit an intercept with sparse inputs. Either set the solver to "auto" or "sparse_cg", or set a low "tol" and a high "max_iter" (especially if inputs are not standardized).
  warnings.warn(
/Users/madhuranirale/opt/anaconda3/lib/python3.

[CV 3/5] END ridge__alpha=0.01, ridge__fit_intercept=False, ridge__solver=svd;, score=nan total time=   1.1s
[CV 3/5] END ridge__alpha=0.1, ridge__fit_intercept=True, ridge__solver=cholesky;, score=nan total time=   0.7s
[CV 4/5] END ridge__alpha=1, ridge__fit_intercept=True, ridge__solver=sparse_cg;, score=-0.878 total time=   1.9s
[CV 4/5] END ridge__alpha=0.01, ridge__fit_intercept=False, ridge__solver=sag;, score=-1.642 total time=   5.2s
[CV 1/5] END ridge__alpha=0.001, ridge__fit_intercept=False, ridge__solver=saga;, score=-1.294 total time=   3.5s
[CV 3/5] END ridge__alpha=0.001, ridge__fit_intercept=True, ridge__solver=cholesky;, score=nan total time=   0.8s
[CV 4/5] END ridge__alpha=0, ridge__fit_intercept=True, ridge__solver=sag;, score=-0.897 total time=   6.0s
[CV 4/5] END ridge__alpha=0.1, ridge__fit_intercept=True, ridge__solver=saga;, score=nan total time=   0.8s
[CV 1/5] END ridge__alpha=0.1, ridge__fit_intercept=False, ridge__solver=svd;, score=nan total time=   0.8s
[

/Users/madhuranirale/opt/anaconda3/lib/python3.9/site-packages/sklearn/linear_model/_ridge.py:729: UserWarning: "sag" solver requires many iterations to fit an intercept with sparse inputs. Either set the solver to "auto" or "sparse_cg", or set a low "tol" and a high "max_iter" (especially if inputs are not standardized).
  warnings.warn(
/Users/madhuranirale/opt/anaconda3/lib/python3.9/site-packages/sklearn/linear_model/_ridge.py:729: UserWarning: "sag" solver requires many iterations to fit an intercept with sparse inputs. Either set the solver to "auto" or "sparse_cg", or set a low "tol" and a high "max_iter" (especially if inputs are not standardized).
  warnings.warn(
/Users/madhuranirale/opt/anaconda3/lib/python3.9/site-packages/sklearn/linear_model/_ridge.py:729: UserWarning: "sag" solver requires many iterations to fit an intercept with sparse inputs. Either set the solver to "auto" or "sparse_cg", or set a low "tol" and a high "max_iter" (especially if inputs are not standardi

RandomizedSearchCV(cv=5,
                   estimator=Pipeline(steps=[('functiontransformer',
                                              FunctionTransformer(func=<function _encode_dates at 0x7f8a640971f0>)),
                                             ('columntransformer',
                                              ColumnTransformer(transformers=[('date',
                                                                               OneHotEncoder(handle_unknown='ignore'),
                                                                               ['year',
                                                                                'month',
                                                                                'day',
                                                                                'weekday',
                                                                                'hour']),
                                                                       

In [34]:
# get the best parameters from the RandomizedCV
bestparams1 = rscv.best_params_
bestparams1

{'ridge__solver': 'sparse_cg', 'ridge__fit_intercept': True, 'ridge__alpha': 1}

In [35]:
# store the pipeline and bestparams
joblib.dump(pipe, 'Ridge')
joblib.dump(bestparams1, 'Ridge_Low_Alpha')

['Ridge_Low_Alpha']

In [36]:
# calulate the rmse and r-squared errors on the fit using best params

rmse_train = mean_squared_error(y_train, rscv.predict(X_train), squared=False)
rmse_test = mean_squared_error(y_test, rscv.predict(X_test), squared=False)
r2_train = r2_score(y_train, rscv.predict(X_train))
r2_test = r2_score(y_test, rscv.predict(X_test))

print(
    f"Train set, RMSE={rmse_train:.7f}"
)
print(
    f"Test set, RMSE={rmse_test:.7f}"
)

print(
    f"Train set, r2 score={r2_train:.7f}"
)
print(
    f"Test set, r2 score={r2_test:.7f}"
)

Train set, RMSE=0.7883760
Test set, RMSE=0.7293973
Train set, r2 score=0.7785142
Test set, r2 score=0.7431063


In [37]:
params = {
 'ridge__alpha': [1460, 1465, 1470, 1475, 1480, 1485, 1490, 1495, 1500]
}

regressor = Ridge()
pipe = make_pipeline(date_encoder, preprocessor, regressor)
rscv = RandomizedSearchCV(pipe, param_distributions=params, n_iter=5, scoring="neg_root_mean_squared_error", n_jobs=-1, cv=5, verbose=3)
rscv.fit(X_train, y_train)

Fitting 5 folds for each of 5 candidates, totalling 25 fits


RandomizedSearchCV(cv=5,
                   estimator=Pipeline(steps=[('functiontransformer',
                                              FunctionTransformer(func=<function _encode_dates at 0x7f8a640971f0>)),
                                             ('columntransformer',
                                              ColumnTransformer(transformers=[('date',
                                                                               OneHotEncoder(handle_unknown='ignore'),
                                                                               ['year',
                                                                                'month',
                                                                                'day',
                                                                                'weekday',
                                                                                'hour']),
                                                                       

In [38]:
# get the best parameters from the RandomizedCV
bestparams2 = rscv.best_params_
bestparams2

{'ridge__alpha': 1500}

In [39]:
# store the pipeline and bestparams
joblib.dump(pipe, 'Ridge')
joblib.dump(bestparams2, 'Ridge_Large_Alpha')

['Ridge_Large_Alpha']

In [40]:
# calulate the rmse and r-squared errors on the fit using best params

rmse_train = mean_squared_error(y_train, rscv.predict(X_train), squared=False)
rmse_test = mean_squared_error(y_test, rscv.predict(X_test), squared=False)
r2_train = r2_score(y_train, rscv.predict(X_train))
r2_test = r2_score(y_test, rscv.predict(X_test))

print(
    f"Train set, RMSE={rmse_train:.7f}"
)
print(
    f"Test set, RMSE={rmse_test:.7f}"
)

print(
    f"Train set, r2 score={r2_train:.7f}"
)
print(
    f"Test set, r2 score={r2_test:.7f}"
)

Train set, RMSE=0.7912422
Test set, RMSE=0.7290802
Train set, r2 score=0.7769008
Test set, r2 score=0.7433296
